In [1]:
import numpy as np
import polars as pl

import altair as alt
from altair import datum
import vegafusion as vf
vf.enable(row_limit=100000)

vegafusion.enable(mimetype='html', row_limit=100000, embed_options=None)

In [2]:
df = pl.scan_parquet('../../m5out/trace_gcc_lto.parquet', low_memory=True, cache=False)

In [3]:
df.fetch(n_rows=3)

shape: (3, 12)
┌────────┬───────────┬───────────┬────────────┬───┬───────┬───────────┬──────────────┬─────────────┐
│ tick   ┆ disassemb ┆ inst_addr ┆ inst_rel_a ┆ … ┆ taken ┆ ras       ┆ regs         ┆ ras_rel     │
│ ---    ┆ ly        ┆ ---       ┆ ddr        ┆   ┆ ---   ┆ ---       ┆ ---          ┆ ---         │
│ u64    ┆ ---       ┆ u64       ┆ ---        ┆   ┆ bool  ┆ list[u64] ┆ struct[15]   ┆ list[str]   │
│        ┆ str       ┆           ┆ str        ┆   ┆       ┆           ┆              ┆             │
╞════════╪═══════════╪═══════════╪════════════╪═══╪═══════╪═══════════╪══════════════╪═════════════╡
│ 227000 ┆ bl   <__l ┆ 4201492   ┆ _start+48  ┆ … ┆ false ┆ []        ┆ {0,549755748 ┆ []          │
│        ┆ ibc_start ┆           ┆            ┆   ┆       ┆           ┆ 219,0,0,0,0, ┆             │
│        ┆ _main>    ┆           ┆            ┆   ┆       ┆           ┆ 0,0,0,0,…    ┆             │
│ 454000 ┆ cbz   x7, ┆ 5453436   ┆ __libc_sta ┆ … ┆ true  ┆ [4201492] ┆ {4195664,16, ┆ ["_start+48 │
│        ┆ <__libc_s ┆           ┆ rt_main+3c ┆   ┆       ┆           ┆ 549755747448 ┆ "]          │
│        ┆ tart_main ┆           ┆            ┆   ┆       ┆           ┆ ,5455112…    ┆             │
│        ┆ +7…       ┆           ┆            ┆   ┆       ┆           ┆              ┆             │
│ 562000 ┆ cbnz      ┆ 5453500   ┆ __libc_sta ┆ … ┆ false ┆ [4201492] ┆ {4195664,16, ┆ ["_start+48 │
│        ┆ x1, <__li ┆           ┆ rt_main+7c ┆   ┆       ┆           ┆ 549755747448 ┆ "]          │
│        ┆ bc_start_ ┆           ┆            ┆   ┆       ┆           ┆ ,5455112…    ┆             │
│        ┆ main+…    ┆           ┆            ┆   ┆       ┆           ┆              ┆             │
└────────┴───────────┴───────────┴────────────┴───┴───────┴───────────┴──────────────┴─────────────┘

In [4]:
df.select(pl.count('tick')).collect(streaming=True)

shape: (1, 1)
┌───────────┐
│ tick      │
│ ---       │
│ u32       │
╞═══════════╡
│ 228047598 │
└───────────┘

In [27]:
ddf = df.groupby('inst_rel_addr').agg([
    pl.count(), 
    pl.col('taken').cast(pl.UInt64).mean(),
    pl.col('mispredicted').cast(pl.UInt64).mean()
]).collect(streaming=True)

ddf.columns

['inst_rel_addr', 'count', 'taken', 'mispredicted']

In [6]:
ddf.head()

shape: (5, 4)
┌───────────────────────────────┬───────┬──────────┬──────────────┐
│ inst_rel_addr                 ┆ count ┆ taken    ┆ mispredicted │
│ ---                           ┆ ---   ┆ ---      ┆ ---          │
│ str                           ┆ u32   ┆ f64      ┆ f64          │
╞═══════════════════════════════╪═══════╪══════════╪══════════════╡
│ bcmp+4                        ┆ 10159 ┆ 0.956492 ┆ 0.167733     │
│ build_nt+cc                   ┆ 1450  ┆ 1.0      ┆ 0.206897     │
│ gen_blt+90                    ┆ 50    ┆ 0.58     ┆ 0.0          │
│ basic_induction_var+268       ┆ 104   ┆ 0.0      ┆ 0.0          │
│ add_dependence.constprop.0+34 ┆ 5462  ┆ 0.99762  ┆ 0.0          │
└───────────────────────────────┴───────┴──────────┴──────────────┘

In [10]:
taken_plot = alt.Chart(ddf).mark_circle().encode(
    x = 'taken:Q',
    y = alt.Y(
        'count:Q',
        scale=alt.Scale(type="log")
    ),
    tooltip=['inst_rel_addr:O', 'count:Q', 'total_taken:Q']
).transform_calculate(
    total_taken = 'floor(datum.taken * datum.count)'
).interactive()

logdata = pl.DataFrame({'x': np.linspace(0.0001,1,100,dtype=float), 'y': 1 / np.linspace(0.0001,1,100,dtype=float) })
logplot = alt.Chart(logdata).mark_line(color="#FFAA00").encode(
    x = 'x:Q',
    y = alt.Y(
        'y:Q',
        scale=alt.Scale(type="log")
    )
).interactive()

mispred_plot = alt.Chart(ddf).mark_circle().encode(
    x = 'mispredicted:Q',
    y = alt.Y(
        'count:Q',
        scale=alt.Scale(type="log")
    ),
    tooltip='inst_rel_addr:O'
).interactive()

((logplot+taken_plot) | mispred_plot)


alt.HConcatChart(...)

In [56]:
# m88ksim: execute+98
# gcc: insert_regs+78 build_unary_op+38

bname = 'invalidate.lto_priv.0+290'

ddf = df.filter(pl.col('inst_addr') == 4988244) \
    .groupby(pl.col('ras').arr.head(1)) \
    .agg([
        pl.count(),
        pl.col('taken').cast(pl.UInt64).mean(),
        pl.col('mispredicted').cast(pl.UInt64).mean()
    ]).filter(pl.col('count') > 10).collect()
ddf.head()

shape: (5, 4)
┌───────────┬───────┬──────────┬──────────────┐
│ ras       ┆ count ┆ taken    ┆ mispredicted │
│ ---       ┆ ---   ┆ ---      ┆ ---          │
│ list[u64] ┆ u32   ┆ f64      ┆ f64          │
╞═══════════╪═══════╪══════════╪══════════════╡
│ [4267896] ┆ 960   ┆ 0.0      ┆ 0.553125     │
│ [4734936] ┆ 36    ┆ 0.0      ┆ 0.138889     │
│ [5056472] ┆ 1051  ┆ 0.242626 ┆ 0.360609     │
│ [5155900] ┆ 51    ┆ 0.0      ┆ 0.333333     │
│ [5157404] ┆ 18    ┆ 0.0      ┆ 0.166667     │
└───────────┴───────┴──────────┴──────────────┘

In [17]:
df.filter(pl.col('inst_rel_addr') == bname).select(pl.count('inst_rel_addr')).collect(streaming=True)

shape: (1, 1)
┌───────────────┐
│ inst_rel_addr │
│ ---           │
│ u32           │
╞═══════════════╡
│ 24654         │
└───────────────┘

In [21]:
alt.Chart(ddf).mark_circle().encode(
    x = 'mispredicted:Q',
    y = alt.Y(
        'count:Q',
        scale=alt.Scale(type="log")
    ),
    tooltip='inst_rel_addr:O'
).transform_filter(
    (datum.taken >= 0.25) & (datum.taken <= 0.75)
).interactive()

alt.Chart(...)

In [49]:
bns = df.filter(pl.count('tick') > 1000) \
        .groupby(pl.col('inst_addr')) \
        .agg(pl.col('mispredicted').cast(pl.UInt64).mean()) \
        .filter(pl.col('mispredicted') > 0.4) \
        .select(pl.col('inst_addr')).collect(streaming=True)['inst_addr']

ddf2 = df.filter(pl.col('inst_addr').is_in(bns)) \
    .groupby([pl.col('inst_rel_addr'), pl.col('inst_addr'), pl.col('ras').arr.first()]) \
    .agg([
        pl.count(), 
        pl.col('taken').cast(pl.UInt64).mean()
    ]) \
    .filter(pl.col('count') > 50) \
    .groupby(pl.col('inst_rel_addr'), pl.col('inst_addr')) \
    .agg(pl.col('taken').std()) \
    .filter(pl.col('taken') > 0.1) \
    .select(pl.col('inst_rel_addr'), pl.col('inst_addr'), pl.col('taken').sort(descending=True)) \
    .collect(streaming=True)
    

In [50]:
ddf2

shape: (165, 3)
┌───────────────────────────────────┬───────────┬──────────┐
│ inst_rel_addr                     ┆ inst_addr ┆ taken    │
│ ---                               ┆ ---       ┆ ---      │
│ str                               ┆ u64       ┆ f64      │
╞═══════════════════════════════════╪═══════════╪══════════╡
│ emit_cmp_insn+13c                 ┆ 4988244   ┆ 0.707107 │
│ try_combine+9d8                   ┆ 4685200   ┆ 0.707107 │
│ build_unary_op+38                 ┆ 5367744   ┆ 0.707107 │
│ find_reloads.constprop.0+1cb0     ┆ 4245272   ┆ 0.707107 │
│ …                                 ┆ …         ┆ …        │
│ try_merge_delay_insns.isra.0.lto… ┆ 4433292   ┆ 0.102418 │
│ layout_type.part.0+58             ┆ 5277928   ┆ 0.101104 │
│ expand_call+394                   ┆ 5062900   ┆ 0.101078 │
│ expand_increment.lto_priv.0+118   ┆ 5086624   ┆ 0.100735 │
└───────────────────────────────────┴───────────┴──────────┘